## Ceph installation on one node.

The latest version of Ceph is Quincy.

[Ceph releases](https://docs.ceph.com/en/latest/releases/)


Your node will be the Ceph cluster. Your LXC container will be a client that mounts the Ceph file system.


### Clean Debian 12 installation by FOG.

- Reimage your node with FOG to get clean Debioan 12 install.

1. Schedule Deploy task for your node.
   
   Login to the FOG portral: https://192.168.5.250//fog/
   
   Username: fog
   
   Password: password
   
   
   Navigate to "Hosts"
   
   List all hosts.
   
   In the task column, click onto the green "Deploy" icon.
   
   Click onto Task to schedule a new task.
   
2. Configure your node for Network boot.

   Login to the ADMIN page of your node, https://192.168.5.20x
    where 'x' is your node number.
    
   Click on Remote Control.
   
   Scroll down to iKVM.
   
   Login to the console of your node.
   
   Reboot with Ctr-Alt-Del key combination on the virtual keyboard.
   
   When the system boots up, press F12 on the virtual keyboard.

   The node should boot into the FOG installer, which will start the installation.
   
3. GRUB update.

   The FOG installer shouldn't touch your boot loader, so your node should be able to bootup into the new Debian 12 fine. 
   
   
4. Hostname update.

   On trhe node, edit file ```/etc/hostname``` and fix the node name for the correct one:

```bash
nano /etc/hostname
```

### Preinstallation steps.

- Try SSH to the node.

You'll need to clean the old SSH key in your known_hosts file, then accept the new key.

- Login to the node.

The 3 non-system drives were used for the storage exercises. You need to remove the partition tables on them.

Find out what is your system drive:

```bash
df -h
```

If, for example, it is /dev/sdd, wipe out the partition tables on /dev/sda, /dev/sdb, /dev/sdc:
```bash
wipefs -a /dev/sda
wipefs -a /dev/sdb
wipefs -a /dev/sdc
```

Create user and group ```ceph``` with uid = git =167 to make them consistent with the containers:
```bash
groupadd -g 167 ceph
useradd -m -d /var/lib/ceph -g 167 -u 167 -s /usr/sbin/nologin ceph
```

If it shows that the drives still have LVS labels on them, clear the LVS with the command below:
```bash
ceph-volume lvm zap /dev/sda
ceph-volume lvm zap /dev/sdb
ceph-volume lvm zap /dev/sdc
```

- Install cephadm.

Install curl
```bash
sudo apt install curl
```

Reconfigure the timezone to US/EST
```bash
sudo dpkg-reconfigure tzdata
```

Download ```cephadm``` for Quincy:
```bash
CEPH_RELEASE=17.2.6
curl --silent --remote-name --location https://github.com/ceph/ceph/raw/quincy/src/cephadm/cephadm
```

Make the installation script executable:
```bash
chmod a+x cephadm
```


```bash
sudo -s
./cephadm install
```

```bash
which cephadm
```
If you see ```/usr/sbin/cephadm```, it means you got cephadm installed on the system.


### Bootstrap Ceph cluster.

We are going to use the IP address of eno1 interface for the monitoring service.
Get the IP address of eno1 on your node:
```bash
ip add show eno1
```

Run the ceph bootstrap command. Substitute the IP from above for the \*\<mon-ip\>\* below:

```bash
sudo cephadm bootstrap --mon-ip *<mon-ip>* --dashboard-password-noupdate --initial-dashboard-user admin --initial-dashboard-password password
```

Install Command Line Interface (CLI):
```bash
sudo cephadm install ceph-common
```

Check if the Ceph services are running:
```bash
ceph status
```

same as 
```bash
ceph -s
```

### Ceph configurations.

Most of the Ceph processes are running within containers, and have their own copy of /etc/ceph/ceph.conf file.
Therefore, all the configuration changes should update the files in every container.

Essentially there are three recommended ways for Ceph configuration updates:

A) By using ```ceph config``` command.

B) By using ```get crush map``` dump, decoding it, modifying the txt configuration file, encoding the updated file, then 
 pushing the ```set crush map```.
 
C) By using the GUI portal with limited functionalities.

### One node cluster specifics.

Data replication should be done between the OSD devices only since there are no other nodes.

Check the configuration settings:
```bash
ceph config dump
ceph config get osd
ceph config get osd osd_crush_chooseleaf_type
```

Set ```ceph config get osd osd_crush_chooseleaf_type = 0```. This will prevent the monitor from attempting to 
 store the data replicas on the different nodes:
 
```bash
ceph config set osd osd_crush_chooseleaf_type 0
```



### Ceph configuration via ```crush map dump```. You need to do it only if you are getting HEALTH_WARN.

Check the crush dump rules for OSD:
```bash
ceph osd crush rule dump
```

Get the crush rules into a file comp_crush_map.cm:
```bash
ceph osd getcrushmap -o comp_crush_map.cm
```

We need to install package ceph to get command ```crushtool```:
```bash
cephadm install ceph
```

Decode file comp_crush_map.cm:
```bash
crushtool -d comp_crush_map.cm -o crush_map.cm
```

Edit file crush_map.cm:
```bash
nano crush_map.cm
```

In line 57, replace ```type node``` with ```type osd```.

Encode crush_map.cm:
```bash
crushtool -c crush_map.cm -o new_crush_map.cm
```

Push the configuration change:
```bash
ceph osd setcrushmap -i new_crush_map.cm
```

Run 
```bash
ceph -s
```
See if the ```health: HEALTH_OK``` now.

Otherwise, run 
```bash
ceph health detail
```

### Create OSD.

Clear the LVS labels on the drives with the command below:
```bash
ceph-volume lvm zap /dev/sda
ceph-volume lvm zap /dev/sdb
ceph-volume lvm zap /dev/sdc
```

Create OSD from the available SSD drives on the node:
```
ceph orch apply osd --all-available-devices
```

```bash
ceph config get osd osd_pool_default_pg_num
ceph config get osd osd_pool_default_pgp_num
```

Set ```osd_pool_default_pgp_num = osd_pool_default_pg_num```:

```bash
ceph config set osd osd_pool_default_pgp_num 32
```

### Dashboard.

Login to the dashboard with 
```user: admin```, ```password: password```

Check the cluster status. 
It should be in state HEALTH_OK.

If it gives you HEALTH_WARN state, then most likely you need to fix another setting with replacing the node with osd by using the procedure below.


### Ceph file system setup for sharing.

Create volume ```cephfs```:
```bash
ceph fs volume create cephfs
```

Verify it has been created:
```bash
ceph fs volume ls
```

Setup a key for a user volume access:
```bash
ceph fs authorize cephfs client.user / rw | sudo tee /etc/ceph/ceph.client.user.keyring
```

Create mounting point and mount Ceph file system:
```bash
mkdir /mnt/cephfs
mount -t ceph :/ /mnt/cephfs -o name=user,secret=AQC76phkkEy1JxAA4hvQkHJ8MRu39xJEG+X1QQ==
```
The key above is from file /etc/ceph/ceph.client.user.keyring

It is different in your case.

Save the secret in file /etc/ceph/ceph.client.user.secfile.

Umount the file system, then mount it with referencing the /etc/ceph/ceph.client.user.secfile.

```bash
umount /mnt/cephfs
mount -t ceph :/ /mnt/cephfs -o name=user,secretfile=/etc/ceph/ceph.client.user.secfile
```

### Ceph client setup.

The Ceph client should be setup on the LXC container.

Stop and disable autofs on the LXC container.
```bash
systemctl stop autofs
systemctl disable autofs
```

Configure the timezone for US/Eastern:
```bash
sudo dpkg-reconfigure tzdata
```

Install package for adding 3rd party repositories:
```bash
sudo apt install software-properties-common
```

Add Ceph apt repository:
```bash
sudo -s
wget -q -O- 'https://download.ceph.com/keys/release.asc' | sudo apt-key add -
apt-add-repository 'deb https://download.ceph.com/debian-quincy/ bullseye main'
apt update
```

Install package ```ceph-common```:
```bash
apt install ceph-common
```

Copy the ceph.conf file from the Ceph node:
```bash
scp hostadm@node03:/etc/ceph/ceph.conf /etc/ceph/ceph.conf
```
Note, in your case, the node name above is different.


Copy the secfile from the Ceph node:
```bash
scp hostadm@node03:/etc/ceph/ceph.client.user.secfile /etc/ceph/ceph.client.user.secfile
```

Create the mounting point and mount Ceph file system from the node:
```bash
mkdir /mnt/cephfs
mount -t  ceph node03:/ /mnt/cephfs -o name=user,secretfile=/etc/ceph/ceph.client.user.secfile
```

Check if the file system is mounted:
```bash
df -h
```




### References.


[How Ceph works video](https://www.youtube.com/watch?v=HJivYTJ9Y54)

[Ceph data security video](https://www.youtube.com/watch?v=L5ug8UIs4tI&t=18s)

[Self Balancing and Self Healing video](https://www.youtube.com/watch?v=jBWVcJYNjeA)

[Ceph dashboard video](https://www.youtube.com/watch?v=RUBMj5ORbe4)


[General installation instructions](https://docs.ceph.com/en/quincy/cephadm/install/)

[Ceph configuration commands](https://docs.ceph.com/en/latest/rados/configuration/ceph-conf/)

[Ceph process management](https://access.redhat.com/documentation/en-us/red_hat_ceph_storage/2/html/administration_guide/process_management)

[One node cluster](https://docs.ceph.com/en/quincy/rados/troubleshooting/troubleshooting-pg/#one-node-cluster)

[Setting up a single node Ceph storage cluster](https://balderscape.medium.com/setting-up-a-virtual-single-node-ceph-storage-cluster-d86d6a6c658e)

[Setup an all-in-one Ceph Storage Cluster on one machine](https://www.highgo.ca/2023/03/24/setup-an-all-in-one-ceph-storage-cluster-on-one-machine/)

[Reconfiguring Ceph](https://insujang.github.io/2021-04-23/reconfiguring-ceph/)

